In [1]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import pymrmre
import seaborn as sns
from lifelines import CoxPHFitter
from lifelines.utils import concordance_index
from sklearn.model_selection import train_test_split
from sklearn import preprocessing

In [2]:
pip instalhelp(pymrmre)

/bin/sh: -c: line 0: syntax error near unexpected token `('
/bin/sh: -c: line 0: `/usr/local/anaconda3/bin/python3.7 -m pip instalhelp(pymrmre)'
Note: you may need to restart the kernel to use updated packages.


In [3]:
! pwd

/Users/josephmarsilla/Cervix


In [4]:
select = pd.read_csv('/Users/josephmarsilla/Cervix/Data/Features_with_all_ICC_above_0.5.csv')

In [5]:
len(list(select['Feature']))

758

In [6]:
combined_feat = pd.read_csv('/Users/josephmarsilla/Cervix/Data/final_train_edited.csv')

In [7]:
feats = list(combined_feat)[3:]

In [8]:
feats[0]

'firstorder_InterquartileRange'

In [9]:
edited = combined_feat.drop(columns=['PatientID'])
edited = edited.astype('double')
list_ = []
for i in range(len(edited.iloc[0])):
    list_.append(0)

In [10]:
# help(pymrmre.mrmr_ensemble)

In [11]:
train_set, train_set_target = edited.drop(['event','time'], axis=1), edited[['event','time']]

results = []

In [12]:
# from sklearn import preprocessing
# train_set, test_set, train_set_target,  test_set_target  = train_test_split(train_set, train_set_target, test_size=0.2)
x = train_set.values #returns a numpy array
min_max_scaler = preprocessing.MinMaxScaler()
x_scaled = min_max_scaler.fit_transform(x)
df_train = pd.DataFrame(x_scaled, columns=train_set.columns)
test_scaled = min_max_scaler.transform(test_set)
df_test = pd.DataFrame(test_scaled, columns=train_set.columns)

In [13]:
# print(min_max_scaler.data_max_)

In [24]:
# len(list(train_set))

In [23]:
# train_set_target['event']

In [22]:
# list(train_set.isnull().sum())

In [29]:
# test pymrmre
# s1 = pymrmre.mrmr_ensemble(features=train_set, targets=train_set_target.drop(columns='time'),
#                            solution_length=10, solution_count=1)

In [30]:
# s1.iloc[0][0]

In [12]:
# train_set_target_['event']
a = list(train_set)
train_set[a[0]].std()

0.11918418899593884

In [14]:
results = []
for itter_num in range(100):
    
    train_set_, test_set_, train_set_target_,  test_set_target_  = train_test_split(train_set, train_set_target, test_size=0.2)
    #test_set, test_set_target = data_opc2.drop(['event','time'], axis=1), opc2_target
    #     fixed_features = ['Age','Sex','ECOG PS','Smoking Hx','Drinking hx','T','N','Stage']
    #     category_features = ['Sex','ECOG PS','Smoking Hx','Drinking hx','T','N','Stage']
    counts = [1]
    result= { 1:[[], [],[],[]]}
    
    # stats = []
    # z-score normalization...
    a = list(train_set_)
    for i,val in enumerate(a):
        me = train_set_[val].mean()
        stds = train_set_[val].std()
        train_set_[val] = (train_set_[val] - me)/stds
        test_set_[val] = (test_set_[val] - me)/stds
        # stats.append((me,stds))

    for j, c in enumerate(counts):
        cindices = []
        print("The current solution count is", c)
        for l in range(1, 41):

            #print("The current features selected length is", length)
            #print("Now we are testing the cox model with fixed")

            avg_c1, avg_c2 = 0.0, 0.0
            print('Hey')
            
            s1 = pymrmre.mrmr_ensemble(features=train_set_, targets = train_set_target_.drop(columns='time'),
                                       solution_length=l, solution_count=c)

#             s1 = mrmr.mrmr_ensemble_survival(features = train_set,
#                                              targets = train_set_target,
#                                              category_features = category_features,
#                                              fixed_features = fixed_features,
#                                              solution_count = c,
#                                              solution_length = l)

#             x = train_set_.values #returns a numpy array
#             min_max_scaler = preprocessing.MinMaxScaler()
#             x_scaled = min_max_scaler.fit_transform(x)
#             train_set_ = pd.DataFrame(x_scaled, columns=train_set_.columns)
#             test_scaled = min_max_scaler.transform(test_set_.values)
#             test_set_ = pd.DataFrame(test_scaled, columns=train_set_.columns)


            for i in range(c):
        
                train_mrmr = train_set_[s1.iloc[0][i]]

#                 vals = []
#                 for val in list(s1.iloc[0][i]):
#                     # scaler = preprocessing.MinMaxScaler()
#                     vals.append((train_mrmr[val].min(), train_mrmr[val].max()))
#                     train_mrmr[val] = train_mrmr[val] - train_mrmr[val].min()/train_mrmr[val].max()

                train_mrmr['event'] = train_set_target_['event']
                train_mrmr['time'] = train_set_target_['time']
                # print(train_mrmr.isnull().sum())
                test_mrmr = test_set_[s1.iloc[0][i]]
                
#                 for i, val in enumerate(list(s1.iloc[0][i])):
#                     test_mrmr[val] = (test_mrmr[val] - vals[i][0])/vals[i][1] 
                
                test_mrmr['event'] = test_set_target_['event']
                test_mrmr['time'] = test_set_target_['time']
                # print(test_mrmr.isnull().sum())

                # what if we run on pre-normalized data?
                # can normalize it...
                cph1 = CoxPHFitter() #penalizer=0.01
                cph1.fit(train_mrmr, duration_col='time', event_col='event', show_progress=False, step_size=0.50)
                c1 = concordance_index(test_mrmr['time'], -cph1.predict_partial_hazard(test_mrmr).values, test_mrmr['event'])
                avg_c1 += c1
                #print("The current c-index for model-1 is", c1)
            
            avg_c1 /= c
            

            cindices.append(avg_c1)
        
        result[c] = cindices
        print("The analysis of this solution count is all done!")
        print(cindices)
        # break
    
    results.append(result)
    print("All done!")
    # break

/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


The current solution count is 1
Hey
Hey
Hey


/usr/local/anaconda3/lib/python3.7/site-packages/pymrmre/MrmreFilter.py:158: RuntimeWarning: invalid value encountered in greater
  causality_dropped = np.where(np.array(self._causality_list.loc[target_index]) > causality_threshold)
/usr/local/anaconda3/lib/python3.7/site-packages/pymrmre/MrmreFilter.py:159: RuntimeWarning: invalid value encountered in less
  mi_dropped = np.where(-.5 * np.log(1 - np.square(self._mi_matrix[:, target_index])) < mi_threshold)
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:60: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usin

Hey
Hey


/usr/local/anaconda3/lib/python3.7/site-packages/pymrmre/MrmreFilter.py:158: RuntimeWarning: invalid value encountered in greater
  causality_dropped = np.where(np.array(self._causality_list.loc[target_index]) > causality_threshold)
/usr/local/anaconda3/lib/python3.7/site-packages/pymrmre/MrmreFilter.py:159: RuntimeWarning: invalid value encountered in less
  mi_dropped = np.where(-.5 * np.log(1 - np.square(self._mi_matrix[:, target_index])) < mi_threshold)
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:60: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usin

...

/usr/local/anaconda3/lib/python3.7/site-packages/pymrmre/MrmreFilter.py:158: RuntimeWarning: invalid value encountered in greater
  causality_dropped = np.where(np.array(self._causality_list.loc[target_index]) > causality_threshold)
/usr/local/anaconda3/lib/python3.7/site-packages/pymrmre/MrmreFilter.py:159: RuntimeWarning: invalid value encountered in less
  mi_dropped = np.where(-.5 * np.log(1 - np.square(self._mi_matrix[:, target_index])) < mi_threshold)
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:60: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:61: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usin

Hey
Hey


/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:68: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:69: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/usr/local/anaconda3/lib/python3.7/site-packages/lifelines/fitters/coxph_fitter.py:701: ConvergenceWarning: Newton-Rhaphson failed to converge sufficiently in 500 steps.

  warnings.warn("Newton-Rhaphson failed to converge sufficiently in %d steps.\n" % max_steps, Convergen

Hey
The analysis of this solution count is all done!
[0.5664739884393064, 0.5606936416184971, 0.5606936416184971, 0.5664739884393064, 0.6011560693641619, 0.5895953757225434, 0.5895953757225434, 0.6011560693641619, 0.653179190751445, 0.5838150289017341, 0.5895953757225434, 0.5838150289017341, 0.5780346820809249, 0.5838150289017341, 0.6011560693641619, 0.5895953757225434, 0.5549132947976878, 0.6416184971098265, 0.6358381502890174, 0.6358381502890174, 0.6127167630057804, 0.6184971098265896, 0.6589595375722543, 0.630057803468208, 0.6473988439306358, 0.653179190751445, 0.6242774566473989, 0.5953757225433526, 0.5780346820809249, 0.48554913294797686, 0.4797687861271676, 0.4393063583815029, 0.43352601156069365, 0.43352601156069365, 0.43352601156069365, 0.4046242774566474, 0.41040462427745666, 0.41040462427745666, 0.5433526011560693, 0.5780346820809249]
All done!


/usr/local/anaconda3/lib/python3.7/site-packages/lifelines/fitters/coxph_fitter.py:701: ConvergenceWarning: Newton-Rhaphson failed to converge sufficiently in 500 steps.

  warnings.warn("Newton-Rhaphson failed to converge sufficiently in %d steps.\n" % max_steps, ConvergenceWarning)


In [15]:
avg_ci = 0
for ins in results:
    avg_ci += np.array(ins[1])

In [16]:
avg_ci/100

array([0.64769431, 0.64989944, 0.6439187 , 0.63981878, 0.65353003,
       0.65817024, 0.6651854 , 0.66346385, 0.66484255, 0.66865252,
       0.66890791, 0.66931252, 0.66597818, 0.66615414, 0.66891072,
       0.66826685, 0.66735901, 0.66430838, 0.661201  , 0.65977637,
       0.6559542 , 0.65721306, 0.65372159, 0.65464983, 0.65280819,
       0.653364  , 0.65579935, 0.6577958 , 0.6570809 , 0.65746228,
       0.65470884, 0.64701218, 0.64599429, 0.64894831, 0.64938679,
       0.65147457, 0.65658975, 0.65368267, 0.65202399, 0.64874982])